# Choropleth plotting

An example notebook to familiarise myself with and experiment with some of Foliums choropleth plotting capabilities

To start out, use foliums basic `Map` method which takes Latitude and longitude and plots a basic GPS map, complete with labels and scrollable action
The Map function also offers the option to change the tiling format (it will default to the OpenStreemMap format, that used by the likes of Google Maps and Apple Maps)

We can also save this to a html document to be sharable

In [120]:
import folium
from folium import plugins
import json
import requests
import geopandas as gpd
import os

import seaborn as sns; sns.set()
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np

In [2]:
map_types = ['Stamen Terrain', 'Stamen Toner', 'Cartodb Positron']

boston = folium.Map(location=[42.36114, -71.05708], tiles=map_types[0], zoom_start=10)
boston

#boston.save('bostom_map.html')

Foliums map structure works much like a layering system, where we can define features and add them to the base map layer. A good example would be markers for specifying specific coordinates

Theres are multiple libraries available for all manner of tooltip icons that you could need to employ in map generation. For this, I mostly just use the ones listed in the [FontAwesome library](https://fontawesome.com/icons?d=gallery)

In [126]:
boston = folium.Map(location=[42.36114, -71.05708], tiles=map_types[0], zoom_start=10)

folium.Marker([42.3769, -71.0606], popup='<i>Bunker Hill</i>', tooltip="Bunker Hill Monument", icon=folium.Icon(color='red', icon='landmark', prefix='fa')).add_to(boston)
folium.Marker([42.3569, -71.0656], popup='<i>Boston Common</i>', tooltip="Boston Common", icon=folium.Icon(color='blue', icon='tree', prefix='fa')).add_to(boston)
folium.Marker([42.3615, -71.0580], popup='<i>Boston City Hall</i>', tooltip="Boston City Hall", icon=folium.Icon(color='green', icon='city', prefix='fa')).add_to(boston)
folium.Marker([42.3398, -71.0939], popup='<i>Boston Museum of Fine Art</i>', tooltip="Museum of Fine Art", icon=folium.Icon(color='red', icon='museum', prefix='fa')).add_to(boston)

mini = plugins.MiniMap() #add a minimap, just because
mini.add_to(boston)

boston

In [123]:
bound = folium.GeoJson('./City_of_Boston_Boundary.geojson', name="City Boundary")
bound.add_to(boston)

boston

Can see its realtively simple to generate folum maps and apply layers of geoJSON data to them and also change the styling of said layers

But would also be instructive to try some more complete geospatial plotting
Ive taken a dataset from the Analyze Boston open-source data site where you can find a large variety of datasets for various aspectes and areas of the Boston area. For this I picked the [CLIMATE READY BOSTON SOCIAL VULNERABILITY
](https://data.boston.gov/dataset/climate-ready-boston-social-vulnerability) set. It is a set of geographically linked data collecting social statistics as a means of guaging susceptibility of specific groups in cities (here, Boston) to events that may stress city resilence i.e. Climate change exaserbated flooding, seasonal storms, heatwaves etc.

In [104]:
boston = folium.Map(location=[42.36114, -71.05708], tiles=map_types[0], zoom_start=10)

climate_geo = './Climate_Ready_Boston_Social_Vulnerability.geojson'
climate_shp = './Climate_Ready_Boston_Social_Vulnerability-shp/c7230a7a-4081-4743-b911-e18f66e1beca2020330-1-17gw6be.a4ds.shp'
climate_dat = './Climate_Ready_Boston_Social_Vulnerability.csv'


climate_geo_data = gpd.read_file(climate_geo)
climate_shp_data = gpd.read_file(climate_shp)
climate_overview_data = pd.read_csv(climate_dat)

In [105]:
climate_geo_data.head()


FID      GEOID10   AREA_SQFT  AREA_ACRES  POP100_RE  HU100_RE  TotDis  \
0    1  25025010405  3914567.54     89.8661       5522       994     470   
1    2  25025010404  1472713.92     33.8089       5817      1862     299   
2    3  25025010801  1376667.12     31.6039       2783      1899      84   
3    4  25025010702  3228780.12     74.1226       2400      1643      45   
4    5  25025010204  2741497.18     62.9361       3173      1283     131   

   TotChild  OlderAdult  Low_to_No   LEP  POC2  MedIllnes          Name  \
0        60         331       1191  1522  1755    2131.22  Mission Hill   
1        77          56       2387  2443  1749    2201.14        Fenway   
2       281         390         72   462   447    1214.76      Back Bay   
3        86         285        187   472   320    1014.20      Back Bay   
4        13          36        895   931  1039    1181.78        Fenway   

     Shape__Area  Shape__Length  \
0  666100.000000    6036.192907   
1  250612.382812    2176.592171   
2  234357.910156    2542.043078   
3  549614.007812    3224.573044   
4  466585.238281    3143.610637   

                                            geometry  
0  POLYGON ((-71.08997 42.34393, -71.09020 42.343...  
1  POLYGON ((-71.08580 42.34334, -71.08505 42.342...  
2  POLYGON ((-71.07251 42.35546, -71.07230 42.355...  
3  POLYGON ((-71.07066 42.35186, -71.07046 42.351...  
4  POLYGON ((-71.10114 42.34777, -71.10087 42.347...

We now have the data from the geoJSON loaded into a geopandas dataframe
We can do an initial overview of the data with the `.explore` method, where we can pick a specific feature to plot in terms of geographic variation

In [109]:
climate_geo_data.columns

Index(['FID', 'GEOID10', 'AREA_SQFT', 'AREA_ACRES', 'POP100_RE', 'HU100_RE',
       'TotDis', 'TotChild', 'OlderAdult', 'Low_to_No', 'LEP', 'POC2',
       'MedIllnes', 'Name', 'Shape__Area', 'Shape__Length', 'geometry'],
      dtype='object')

In [112]:
b = climate_geo_data.explore(column = "OlderAdult", name="Older Adult")
folium.LayerControl().add_to(b)

b

In [137]:
#Create base map
bos_city = folium.Map(location=[42.36114, -71.05708], zoom_start=11)

#Define the choropleth
cpleth = folium.Choropleth(geo_data= climate_geo_data,        # The geodataframe containing the actual geometry
                          data= climate_geo_data,             # The dataframe containing the features and numberic info (can be the same as geodata)
                          key_on='feature.properties.Name',   # The feature from the geodata parameter that links the two tables (will always start with `feature`)
                          columns=['Name','POP100_RE','POC2','TotChild'], #The features to include as popups on the map
                          fill_color='RdYlGn',
                          legend_name='Population',
                          name='Boston city climate readiness')

#Define tooltip, the popup when hovered over that displayes speficied feature values
tooltip = folium.features.GeoJsonTooltip(fields=['Name','POP100_RE','POC2','TotChild'],
                                        aliases=['Neighbourhood', 'Population', 'People of Color', 'Child pop.'],
                                        labels=True,
                                        sticky=False)

cpleth.geojson.add_child(tooltip)
cpleth.add_to(bos_city)
folium.LayerControl().add_to(bos_city)



In [138]:
bos_city